# Início

In [1]:
import plotly.express as px
import plotly.graph_objects as go
import numpy as np
import pandas as pd
import copy
from tqdm import tqdm
import time
import os
from scipy import signal
from sklearn.model_selection import train_test_split
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import accuracy_score
from sklearn.decomposition import PCA
from natsort import natsorted

In [121]:
files = ['acc_climbingup_forearm.csv',
         'acc_climbingup_waist.csv',
         'acc_walking_forearm.csv',
         'acc_walking_waist.csv']
s = [None] * len(files)
for i, path in enumerate(files):
    data = pd.read_csv(path)
    s[i] = data['attr_x'].to_numpy()
    s[i] = s[i][:26938]
    s[i] = s[i] - s[i].mean()
    s[i] = s[i]/30


In [122]:
fig = go.Figure()
for i, x in enumerate(s):
    fig.add_trace(go.Scatter(y=x, mode="lines", showlegend=True, name=files[i]))
fig.show()

In [6]:
def picotar(x, J, passo):
    N = x.shape[0]
    Nj = (N-J)//passo + 1
    X = np.zeros((Nj, J))
    for i in range(Nj):
        X[i,:] = x[(i*passo):(i*passo+J)]
    return X

In [11]:
def pcabase(X):
    M = np.ones((X.shape[0],1)).dot(X.mean(axis=0).reshape(1,X.shape[1]))
    R = (X-M).transpose().dot(X-M)
    l, vet = np.linalg.eig(R)
    inds = np.argsort(l)
    vet = vet[:,inds][:,::-1]
    return l, vet

In [21]:
J = 150
passo = 50
X = picotar(s[0], J, passo)
l, vet = pcabase(X)

In [22]:
fig = px.line(vet[:,:5], range_y=[-1/5,1/5])
fig.show()
fig = px.scatter(l.cumsum()/l.sum(), range_y=[0,1.1])
fig.show()

In [23]:
d = 30
W = vet[:,:d]

In [24]:
i = 100
X = picotar(s[0], J, passo)
x = X[i,:]
S = x.dot(W)
xh = S.dot(W.transpose())
fig = px.line(xh)
fig.add_trace(go.Scatter(y=x, mode='lines', showlegend=True))

In [ ]:
class MLP(nn.Module):
    def __init__(self):
        super().__init__()

        self.all_layers = torch.nn.Sequential(

            # 1st hidden layer
            nn.Flatten(start_dim=1),
            nn.Linear(300, 100),
            nn.Tanh(),

            # 2nd hidden layer
            nn.Linear(100, 2)
            # nn.Softmax(dim=1),

#             # output layer
#             nn.Linear(15, num_classes),
        )

    def forward(self, x):
        logits = self.all_layers(x)
        return logits

In [ ]:
def ajusteDados(X):
    N = X.shape[0]
    Nj = X.shape[2]
    S = np.zeros((N*(Nj-151), 2, 150))
    y = np.zeros((N*(Nj-151), 2))
    for i in range(N):
        for j in range(Nj-151):
            S[(i*(Nj-151)+j),:,:] = X[i,:,j:(j+150)]
            y[(i*(Nj-151)+j),:] = X[i,:,(j+150)]
    return S, y

In [ ]:
ordem = 12
w1, w2 = predlin(D[3], ordem)

# Exp 1

In [71]:
files

['acc_climbingup_forearm.csv',
 'acc_climbingup_waist.csv',
 'acc_walking_forearm.csv',
 'acc_walking_waist.csv']

In [163]:
J = 100
passo = 100
Xtr1 = np.concatenate((picotar(s[0][-13000:], J, passo), picotar(s[2][-13000:], J, passo)))
Xtr2 = np.concatenate((picotar(s[1][-13000:], J, passo), picotar(s[3][-13000:], J, passo)))
Xte1 = np.concatenate((picotar(s[0][:13000], J, passo), picotar(s[2][:13000], J, passo)))
Xte2 = np.concatenate((picotar(s[1][:13000], J, passo), picotar(s[3][:13000], J, passo)))
N = Xtr1.shape[0]
y = (np.arange(N)<N//2).astype(int)
print(N)

260


In [164]:
l, vet = pcabase(np.concatenate((Xtr1, Xtr2)))
fig = px.line(vet[:,:5], range_y=[-1/5,1/5])
fig.show()
fig = px.scatter(l.cumsum()/l.sum(), range_y=[0,1.1])
fig.show()

In [166]:
d = 40
W = vet[:,:d]
Str1 = Xtr1.dot(W)
Str2 = Xtr2.dot(W)
Ste1 = Xte1.dot(W)
Ste2 = Xte2.dot(W)

In [171]:
neigh = KNeighborsClassifier(n_neighbors=3)
neigh.fit(Xtr1, y)
df = pd.DataFrame(0, index=['Treino', 'Teste'], columns=['pulso', 'cintura'])
y_pred = neigh.predict(Xtr1)
df.iloc[0,0] = accuracy_score(y, y_pred)
y_pred = neigh.predict(Xtr2)
df.iloc[0,1] = accuracy_score(y, y_pred)
y_pred = neigh.predict(Xte1)
df.iloc[1,0] = accuracy_score(y, y_pred)
y_pred = neigh.predict(Xte2)
df.iloc[1,1] = accuracy_score(y, y_pred)
df

pulso   cintura
Treino  0.930769  0.826923
Teste   0.807692  0.742308

In [172]:
neigh = KNeighborsClassifier(n_neighbors=3)
neigh.fit(Str1, y)
df = pd.DataFrame(0, index=['Treino', 'Teste'], columns=['pulso', 'cintura'])
y_pred = neigh.predict(Str1)
df.iloc[0,0] = accuracy_score(y, y_pred)
y_pred = neigh.predict(Str2)
df.iloc[0,1] = accuracy_score(y, y_pred)
y_pred = neigh.predict(Ste1)
df.iloc[1,0] = accuracy_score(y, y_pred)
y_pred = neigh.predict(Ste2)
df.iloc[1,1] = accuracy_score(y, y_pred)
df

pulso   cintura
Treino  0.926923  0.815385
Teste   0.800000  0.723077

In [173]:
x = Xte1[51,:]
xh = x.dot(W).dot(W.transpose())

fig = px.line(x)
fig.add_trace(go.Scatter(y=xh, mode='lines', showlegend=True))

In [174]:
Ctr1 = np.zeros_like(Xtr1)
Ctr2 = np.zeros_like(Xtr2)
Cte1 = np.zeros_like(Xte1)
Cte2 = np.zeros_like(Xte2)
for i in range(Cte1.shape[0]):
    Ctr1[i,:] = np.correlate(Xtr1[i,:], Xtr1[i,:], 'full')[-J:]
    Ctr2[i,:] = np.correlate(Xtr2[i,:], Xtr2[i,:], 'full')[-J:]
    Cte1[i,:] = np.correlate(Xte1[i,:], Xte1[i,:], 'full')[-J:]
    Cte2[i,:] = np.correlate(Xte2[i,:], Xte2[i,:], 'full')[-J:]
    

In [175]:
neigh = KNeighborsClassifier(n_neighbors=3)
neigh.fit(Ctr1, y)
df = pd.DataFrame(0, index=['Treino', 'Teste'], columns=['pulso', 'cintura'])
y_pred = neigh.predict(Ctr1)
df.iloc[0,0] = accuracy_score(y, y_pred)
y_pred = neigh.predict(Ctr2)
df.iloc[0,1] = accuracy_score(y, y_pred)
y_pred = neigh.predict(Cte1)
df.iloc[1,0] = accuracy_score(y, y_pred)
y_pred = neigh.predict(Cte2)
df.iloc[1,1] = accuracy_score(y, y_pred)
df

pulso   cintura
Treino  0.950000  0.900000
Teste   0.803846  0.869231

In [177]:
l, vet = pcabase(np.concatenate((Ctr1, Ctr2)))
d = 10
W = vet[:,:d]
Str1 = Ctr1.dot(W)
Str2 = Ctr2.dot(W)
Ste1 = Cte1.dot(W)
Ste2 = Cte2.dot(W)
fig = px.line(vet[:,:5], range_y=[-1/3,1/3])
fig.show()
fig = px.scatter(l.cumsum()/l.sum(), range_y=[0,1.1])
fig.show()

In [178]:
neigh = KNeighborsClassifier(n_neighbors=3)
neigh.fit(Str1, y)
df = pd.DataFrame(0, index=['Treino', 'Teste'], columns=['pulso', 'cintura'])
y_pred = neigh.predict(Str1)
df.iloc[0,0] = accuracy_score(y, y_pred)
y_pred = neigh.predict(Str2)
df.iloc[0,1] = accuracy_score(y, y_pred)
y_pred = neigh.predict(Ste1)
df.iloc[1,0] = accuracy_score(y, y_pred)
y_pred = neigh.predict(Ste2)
df.iloc[1,1] = accuracy_score(y, y_pred)
df

pulso   cintura
Treino  0.946154  0.834615
Teste   0.800000  0.853846

In [179]:
px.scatter(x=Ste1[:,0], y=Ste1[:,1], color=y.astype(str))

# Preditor linear

In [214]:
def predlin(Xtr):
    X = Xtr1[:,:-1]
    y = Xtr1[:,-1]
    w = np.linalg.inv(X.transpose().dot(X)).dot(X.transpose()).dot(y)
    return w

In [198]:
J = 11
passo = 1
Xtr1 = np.concatenate((picotar(s[0][-13000:], J, passo), picotar(s[2][-13000:], J, passo)))
Xtr2 = np.concatenate((picotar(s[1][-13000:], J, passo), picotar(s[3][-13000:], J, passo)))
Xte1 = np.concatenate((picotar(s[0][:13000], J, passo), picotar(s[2][:13000], J, passo)))
Xte2 = np.concatenate((picotar(s[1][:13000], J, passo), picotar(s[3][:13000], J, passo)))
N = Xtr1.shape[0]
y = (np.arange(N)<N//2).astype(int)
print(N)

25980


In [215]:
w = predlin(Xtr1)
xh = Xtr1[:,:-1].dot(w)
fig = px.line(xh)
fig.add_trace(go.Scatter(y=Xtr1[:,-1], mode='lines', showlegend=True))
fig.add_trace(go.Scatter(y=Xtr1[:,-1]-xh, mode='lines', showlegend=True))